In [90]:
from HeaderP import *

In [91]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

from bokeh.io import output_notebook, show
from bokeh.plotting import figure, output_file
from bokeh.models import ColumnDataSource, Range1d
from bokeh.layouts import gridplot
from bokeh.models import LinearColorMapper, ColorBar
from bokeh.transform import transform
import random
output_notebook()

Loading BokehJS ...

In [96]:
simNo='2_79e12'
select=True

In [97]:
#data=pd.read_pickle('Data/Buck_g'+simNo+'.pkl')
#data=pd.read_pickle('../SecondYear/CannonDR16_cut.pkl')
#select=pd.read_pickle('Data/Buck_g'+simNo+'_apogee_selec.pkl')
#data=pd.merge(data,select[['iords','ofe_scale','feh_scale']],left_on='iords',right_on='iords')
#data.to_pickle('Data/Buck_g'+simNo+'_apogee_selec.pkl')

In [98]:
if simNo=='data':
    data=pd.read_pickle('../SecondYear/CannonDR16_cut.pkl')
    data['z_today']=data['z']
    data['x_today']=data['X']
    data['y_today']=data['Y']
    data['feh_scale']=data['M_H']
    data['ofe_scale']=data['O_FE']
    data['age']=data['Age']
elif select:
    data=pd.read_pickle('Data/Buck_g'+simNo+'_apogee_selec.pkl')
    data['R_bir']=np.sqrt((data['x_birth'])**2+data['y_birth']**2)
    data['R']=np.sqrt((data['x_today'])**2+data['y_today']**2)
    scale_fe=0.250019907951355/np.std(data['feh'])
    scale_o=0.10861970484256744/np.std(data['ofe'])
    data['feh_scale']=data['feh']*scale_fe-0.0906638577580452-np.mean(data['feh'])
    data['ofe_scale']=data['ofe']*scale_o+0.08182460814714432-np.mean(data['ofe'])
elif not select:
    data=pd.read_pickle('Data/Buck_g'+simNo+'.pkl')
    data['R_bir']=np.sqrt((data['x_birth'])**2+data['y_birth']**2)
    data['R']=np.sqrt((data['x_today'])**2+data['y_today']**2)
    scale_fe=0.250019907951355/np.std(data['feh'])
    scale_o=0.10861970484256744/np.std(data['ofe'])
    data['feh_scale']=data['feh']*scale_fe-0.0906638577580452-np.mean(data['feh'])
    data['ofe_scale']=data['ofe']*scale_o+0.08182460814714432-np.mean(data['ofe'])
    select=data.index.values
    random.shuffle(select)
    data=data.iloc[select[:50000]]

In [100]:
if simNo=='data':
    source = ColumnDataSource(data=dict(R=data.R.values, Jphi=data.J_phi.values,
                                    Jr=data.J_R.values,Jz=data.J_z.values,feh=data.feh_scale.values,
                                    ofe=data.ofe_scale.values,age=data.age.values,z=data.z.values,))
else:
    source = ColumnDataSource(data=dict(R=data.R.values, R_bir=data.R_bir.values, Jphi=data.Jz.values,
                                    Jr=data.Jr.values,Jz=data.Jphi.values,feh=data.feh_scale.values,
                                    ofe=data.ofe_scale.values,age=data.age.values,z=data.z.values,
                                   z_bir=data.z_birth.values))

TOOLS = "box_select,lasso_select,help,reset"

# create a new plot and add a renderer (r,z)
left = figure(tools=TOOLS, width=400, height=325, x_range=(0, 20), y_range=(-7.5, 10))
left.add_layout(color_bar, 'right')
left.circle(x='R', y='z', color=transform('age', color_mapper), 
            size=2, source=source)
color_mapper = LinearColorMapper(palette="RdYlBu10", low=0, high=15)
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, location=(0,0),title='Age [Gyr]')
left.xaxis.axis_label = 'R [kpc]'
left.yaxis.axis_label = 'z [kpc]'

# create another plot (Jphi,Jz)
if simNo=='data':
    mid = figure(tools=TOOLS, width=400, height=325, y_axis_type="log",
             x_range=(-4000, 1000), y_range=(0.01, 10000))
else:
    mid = figure(tools=TOOLS, width=400, height=325, y_axis_type="log",
             x_range=(0, 8000), y_range=(0.01, 10000))
    
mid.circle(x='Jphi', y='Jz', color=transform('age', color_mapper), 
            size=2, source=source)
color_mapper = LinearColorMapper(palette="RdYlBu10", low=0, high=15)
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, location=(0,0),title='Age [Gyr]')
mid.add_layout(color_bar, 'right')
mid.xaxis.axis_label = 'Jphi'
mid.yaxis.axis_label = 'Jz'

# create another new plot and add a renderer (Age,Feh)
if simNo=='data':
    right = figure(tools=TOOLS, width=400, height=325, x_range=(0, 15), y_range=(-0.8, 0.6))
else:
    right = figure(tools=TOOLS, width=400, height=325, x_range=(0, 15), y_range=(-1.2, 0.4))

if simNo=='data':
    right.circle(x='age', y='feh', color=transform('R', color_mapper), 
             size=2, source=source)
    color_mapper = LinearColorMapper(palette="RdYlBu10", low=0, high=15)
    color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, location=(0,0),title='R [kpc]')
else:
    right.circle(x='age', y='feh', color=transform('R_bir', color_mapper), 
             size=2, source=source)
    color_mapper = LinearColorMapper(palette="RdYlBu10", low=0, high=20)
    color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, location=(0,0),title='Rbir [kpc]')
right.add_layout(color_bar, 'right')
right.xaxis.axis_label = 'Age [Gyr]'
right.yaxis.axis_label = '[Fe/H]'

# create another new plot and add a renderer (Age,Feh)
if simNo=='data':
    feh = figure(tools=TOOLS, width=400, height=325, x_range=(-0.8, 0.6), y_range=(-0.2, 0.6))
else:
    feh = figure(tools=TOOLS, width=400, height=325, x_range=(-1.2, 0.4), y_range=(-0.2, 0.4))

feh.circle(x='feh', y='ofe', color=transform('age', color_mapper), 
             size=2, source=source)
color_mapper = LinearColorMapper(palette="RdYlBu10", low=0, high=15)
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, location=(0,0),title='Age [Gyr]')
feh.add_layout(color_bar, 'right')
feh.xaxis.axis_label = '[Fe/H]'
feh.yaxis.axis_label = '[O/Fe]'


p = gridplot([[left, right], [mid, feh]])

output_file('bokeh'+simNo+'.html')

show(p)

In [58]:
sum(data['Jphi']<0)

0